## Get data

In [ ]:
# Only use full for Google colab
try:
    import google.colab
    print("Running on Google Colab")
    import subprocess

    def run_command(command):
        """Runs a command line command."""
        process = subprocess.Popen(command, shell=True, stdout=subprocess.PIPE)
        output, err = process.communicate()
        return output.decode("utf-8")

    run_command("wget https://storage.googleapis.com/ztm_tf_course/nlp_getting_started.zip -d sample_data")
    run_command("unzip nlp_getting_started.zip -d sample_data/nlp_getting_started")
    run_command("python -m spacy download en_core_web_sm")  # download english model for spacy
    run_command("wget https://raw.githubusercontent.com/anilkumarKanasani/tensorflow-deep-learning/main/Notebooks/helper_functions.py")
    print("Data Import completed")

except:
    print("Not running on Google Colab")

## Explore Data

In [ ]:
import numpy as np
import pandas as pd
df_train = pd.read_csv("./sample_data/nlp_getting_started/train.csv")
df_test = pd.read_csv("./sample_data/nlp_getting_started/test.csv")

# convert all NaN values to string
df_train['keyword'] = df_train['keyword'].fillna('no_keyword')
df_train['location'] = df_train['location'].fillna('no_location')

df_train.head()

In [ ]:
# cleaning keywords column
# remove %20 from the keywords
df_train['keyword'] = df_train['keyword'].str.replace('%20', ' ')
df_test['keyword'] = df_test['keyword'].str.replace('%20', ' ')
df_train.head()

In [95]:
# cleaning location column, converting location to possible country names and dropping the location column
import spacy
# Load the pre-trained spaCy model for English
nlp = spacy.load('en_core_web_sm')

df_train['country'] = 'no_country'
df_test['country'] = 'no_country'

# create a new column in data frame with country names extracted from location
for i in range(len(df_train)):
    doc = nlp(df_train['location'][i])
    for ent in reversed(doc.ents):
        if ent.label_ == 'GPE':
            df_train['country'][i] = ent.text
            break
        else:
            df_train['country'][i] = 'no_country'


df_test['country'] = 'no_country'
# create a new column in data frame with country names extracted from location
for i in range(len(df_test)):
    try:
        doc = nlp(df_test['location'][i])
    except:
        df_test['location'][i] = 'no_location'
        doc = nlp(df_test['location'][i])
    for ent in reversed(doc.ents):
        if ent.label_ == 'GPE':
            df_test['country'][i] = ent.text
            break
        else:
            df_test['country'][i] = 'no_country'

# drop the location column from both train and test data frames
df_train = df_train.drop('location', axis=1)
df_test = df_test.drop('location', axis=1)


In [97]:
# saving the cleaned data frames
df_train.to_csv('./sample_data/nlp_getting_started/train_cleaned.csv', index=False)
df_test.to_csv('./sample_data/nlp_getting_started/test_cleaned.csv', index=False)

In [123]:
# loading the cleaned data frames
df_train = pd.read_csv('./sample_data/nlp_getting_started/train_cleaned.csv')
df_test = pd.read_csv('./sample_data/nlp_getting_started/test_cleaned.csv')


### Exploring KeyWords

In [124]:
len(df_train), len(df_test)

(7613, 3263)

In [ ]:
# ignore warnings
import warnings
warnings.filterwarnings("ignore")

pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)

# list of keywords
keywords = list(df_train.keyword.unique())

# number of postive and negative targets for each keyword as a dataframe with row sum as total and column sum as total
df_keywords = pd.DataFrame(columns=['keyword', 'positive', 'negative'])
for keyword in keywords:
    df_keywords = df_keywords.append({'keyword': keyword, 'positive': len(df_train[(df_train['target'] == 1) & (df_train['keyword'] == keyword)]), 'negative': len(df_train[(df_train['target'] == 0) & (df_train['keyword'] == keyword)])}, ignore_index=True)

# row sum and column sum
df_keywords.loc['Total'] = df_keywords.sum()
df_keywords['Total'] = df_keywords['positive'] + df_keywords['negative']

df_keywords = df_keywords.sort_values(by='Total', ascending=True)

# drop the index except the Total row
df_keywords['keyword']['Total'] = 'Total'
df_keywords = df_keywords.reset_index(drop=True)

df_keywords

### Exploring location

In [126]:
# convert all countries if it has total count only 1 tweet to no_country
df_train['country'] = df_train['country'].apply(lambda x: 'no_country' if df_train['country'].value_counts()[x] == 1 else x)
df_test['country'] = df_test['country'].apply(lambda x: 'no_country' if df_test['country'].value_counts()[x] == 1 else x)

In [ ]:
# same as above but for countries
countries = list(df_train.country.unique())

df_countries = pd.DataFrame(columns=['country', 'positive', 'negative'])
for country in countries:
    df_countries = df_countries.append({'country': country, 'positive': len(df_train[(df_train['target'] == 1) & (df_train['country'] == country)]), 'negative': len(df_train[(df_train['target'] == 0) & (df_train['country'] == country)])}, ignore_index=True)

df_countries.loc['Total'] = df_countries.sum()
df_countries['Total'] = df_countries['positive'] + df_countries['negative']

df_countries = df_countries.sort_values(by='Total', ascending=True)

# drop the index except the Total row
df_countries['country']['Total'] = 'Total'
df_countries = df_countries.reset_index(drop=True)

df_countries


### Exploring the text

In [ ]:
# extract the url from the text, clean url from the text
import re
def extract_url(text):
    url = re.findall(r'https?://\S+|www\.\S+', text)
    return url

# clean the url from the text
def clean_url(text):
    url = extract_url(text)
    for i in url:
        text = text.replace(i, '')
    return text

# clean the url from the text
df_train['text'] = df_train['text'].apply(lambda x: clean_url(x))
df_test['text'] = df_test['text'].apply(lambda x: clean_url(x))

df_train

In [129]:
# do the same for hashtags, remove # from the hashtag column items
def extract_hashtag(text):
    hashtag = re.findall(r'#\S+', text)
    return hashtag

# create a new column with the url
df_train['hashtag'] = df_train['text'].apply(lambda x: extract_hashtag(x))
df_test['hashtag'] = df_test['text'].apply(lambda x: extract_hashtag(x))

# clean the hashtag from the text
def clean_hashtag(text):
    hashtag = extract_hashtag(text)
    for i in hashtag:
        text = text.replace(i, '')
    return text

# clean the hashtag from the text
df_train['text'] = df_train['text'].apply(lambda x: clean_hashtag(x))
df_test['text'] = df_test['text'].apply(lambda x: clean_hashtag(x))

# remove the # from the hashtag column items
def remove_hashtag(list_of_text):
    removed_list = []
    for text in list_of_text:
        text = text.replace('#', '')
        removed_list.append(text)
    return removed_list

# remove the # from the hashtag column items
df_train['hashtag'] = df_train['hashtag'].apply(lambda x: remove_hashtag(x))
df_test['hashtag'] = df_test['hashtag'].apply(lambda x: remove_hashtag(x))

df_train

id              keyword  \
0         1           no_keyword   
1         4           no_keyword   
2         5           no_keyword   
3         6           no_keyword   
4         7           no_keyword   
5         8           no_keyword   
6        10           no_keyword   
7        13           no_keyword   
8        14           no_keyword   
9        15           no_keyword   
10       16           no_keyword   
11       17           no_keyword   
12       18           no_keyword   
13       19           no_keyword   
14       20           no_keyword   
15       23           no_keyword   
16       24           no_keyword   
17       25           no_keyword   
18       26           no_keyword   
19       28           no_keyword   
20       31           no_keyword   
21       32           no_keyword   
22       33           no_keyword   
23       34           no_keyword   
24       36           no_keyword   
25       37           no_keyword   
26       38           no_keyword   
27       39           no_keyword   
28       40           no_keyword   
29       41           no_keyword   
30       44           no_keyword   
31       48               ablaze   
32       49               ablaze   
33       50               ablaze   
34       52               ablaze   
35       53               ablaze   
36       54               ablaze   
37       55               ablaze   
38       56               ablaze   
39       57               ablaze   
40       59               ablaze   
41       61               ablaze   
42       62               ablaze   
43       63               ablaze   
44       64               ablaze   
45       65               ablaze   
46       66               ablaze   
47       67               ablaze   
48       68               ablaze   
49       71               ablaze   
50       73               ablaze   
51       74               ablaze   
52       76               ablaze   
53       77               ablaze   
54       78               ablaze   
55       79               ablaze   
56       80               ablaze   
57       81               ablaze   
58       82               ablaze   
59       83               ablaze   
60       85               ablaze   
61       86               ablaze   
62       89               ablaze   
63       91               ablaze   
64       92               ablaze   
65       93               ablaze   
66       95               ablaze   
67       96             accident   
68       97             accident   
69       98             accident   
70      100             accident   
71      102             accident   
72      104             accident   
73      105             accident   
74      107             accident   
75      109             accident   
76      110             accident   
77      112             accident   
78      113             accident   
79      114             accident   
80      117             accident   
81      118             accident   
82      119             accident   
83      120             accident   
84      121             accident   
85      126             accident   
86      128             accident   
87      129             accident   
88      130             accident   
89      131             accident   
90      132             accident   
91      133             accident   
92      134             accident   
93      135             accident   
94      136             accident   
95      137             accident   
96      138             accident   
97      139             accident   
98      141             accident   
99      143             accident   
100     144             accident   
101     145             accident   
102     146           aftershock   
103     149           aftershock   
104     151           aftershock   
105     153           aftershock   
106     156           aftershock   
107     157           aftershock   
108     158           aftershock   
109     159           aftershock   
110     160  